In [1]:
import os
import time
import certifi
import requests
import pandas as pd
import xml.etree.ElementTree as ET


In [2]:
base_url = catalog.load('params:oai_extract_options.base_url')
context = catalog.load('params:oai_extract_options.context')

env = 'dev'

print("base_url: ", base_url)
print("context: ", context)

[12/01/25 21:13:39] INFO     Loading data from params:oai_extract_options.base_url             ]8;id=839398;file:///home/pablo/dev/scholar/kedro-scholar/.venv/lib/python3.10/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=550962;file:///home/pablo/dev/scholar/kedro-scholar/.venv/lib/python3.10/site-packages/kedro/io/data_catalog.py#1048\1048]8;;\
                             (MemoryDataset)...                                                                    

                    INFO     Loading data from params:oai_extract_options.context              ]8;id=639298;file:///home/pablo/dev/scholar/kedro-scholar/.venv/lib/python3.10/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=129116;file:///home/pablo/dev/scholar/kedro-scholar/.venv/lib/python3.10/site-packages/kedro/io/data_catalog.py#1048\1048]8;;\
                             (MemoryDataset)...                                                                    

base_url:  https://ri.conicet.gov.ar/oai/
context:  request


In [3]:
def get_oai_response(base_url, verify=None, max_retries=3, backoff_factor=1.0):

    # Usa el bundle de certifi para evitar errores de certificado en requests
    os.environ.setdefault("REQUESTS_CA_BUNDLE", certifi.where())
    os.environ.setdefault("SSL_CERT_FILE", certifi.where())
    VERIFY_SSL = os.getenv("OAI_VERIFY_SSL", "false").lower() == "true"
    CA_BUNDLE = os.getenv("OAI_CA_BUNDLE") or certifi.where()

    verify_param = CA_BUNDLE if VERIFY_SSL else False
    if verify is not None:
        verify_param = verify

    for attempt in range(1, max_retries + 1):
        start_time = time.time()
        response = None
        try:
            response = requests.get(base_url, verify=verify_param)
            elapsed_time = time.time() - start_time
        except requests.RequestException as exc:
            elapsed_time = time.time() - start_time
            print(f"Error en request (intento {attempt}/{max_retries}): {exc}")
        sleep_time = max(elapsed_time, 0.1)
        print(f"Sleeping for {sleep_time:.2f} seconds")
        time.sleep(sleep_time)

        if response and response.status_code == 200:
            return response

        status = response.status_code if response else "sin respuesta"
        print(f"Error: {status} (intento {attempt}/{max_retries})")

        if attempt < max_retries:
            backoff = backoff_factor * attempt
            print(f"Reintentando en {backoff:.2f} segundos...")
            time.sleep(backoff)
    return None


In [4]:
df_cols = catalog.load("intermediate/oai/cols")
df_cols


                    INFO     Loading data from intermediate/oai/cols (CSVDataset)...           ]8;id=661387;file:///home/pablo/dev/scholar/kedro-scholar/.venv/lib/python3.10/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=838460;file:///home/pablo/dev/scholar/kedro-scholar/.venv/lib/python3.10/site-packages/kedro/io/data_catalog.py#1048\1048]8;;\

setSpec                setName           extract_datetime  \
0        col_11336_373      Articulos(BIOMED)  2025-11-28 00:00:00+00:00   
1        col_11336_466       Articulos(CADIC)  2025-11-28 00:00:00+00:00   
2        col_11336_445      Articulos(CAICYT)  2025-11-28 00:00:00+00:00   
3         col_11336_11      Articulos(CASLEO)  2025-11-28 00:00:00+00:00   
4     col_11336_138773  Articulos (CCONFINES)  2025-11-28 00:00:00+00:00   
...                ...                    ...                        ...   
2068   col_11336_73920          Tesis(UNIHDO)  2025-11-28 00:00:00+00:00   
2069   col_11336_73921         Tesis(UNITEFA)  2025-11-28 00:00:00+00:00   
2070   col_11336_48286              undefined  2025-11-28 00:00:00+00:00   
2071   col_11336_48181              undefined  2025-11-28 00:00:00+00:00   
2072   col_11336_64752              undefined  2025-11-28 00:00:00+00:00   

      is_col_set  is_com_set  
0           True       False  
1           True       False  
2           True       False  
3           True       False  
4           True       False  
...          ...         ...  
2068        True       False  
2069        True       False  
2070        True       False  
2071        True       False  
2072        True       False  

[2073 rows x 5 columns]

## Extract identifiers 

In [5]:
def oai_extract_identifiers_by_sets(base_url: str, context: str, env: str, df_set: pd.DataFrame, iteration_limit = 1, verify=None) -> pd.DataFrame:
    records = []
    if env == "dev": iteration_limit = 2 

    col_ids = df_set.loc[:, "setSpec"].tolist()

    for set_id in col_ids:
        iteration_count = 0
        resumption_token = f'oai_dc///{set_id}/0'

        while True:
            if iteration_count >= iteration_limit:
                break

            params = f'/{context}?verb=ListIdentifiers&resumptionToken={resumption_token}'
            url = base_url + params

            print(f"Consultando: {url}")

            response = get_oai_response(url, verify=verify)
            if not response or not response.ok:
                print(f"Error al consultar: {url}")
                break
            
            iteration_count += 1

            xml_content = response.text

            root = ET.fromstring(xml_content)
            ns = { 'oai': 'http://www.openarchives.org/OAI/2.0/' }
        
            record_nodes = root.findall('.//oai:header', ns)

            if not record_nodes:
                print("No se encontraron más registros.")
                break

            for record in record_nodes:
                
                # Valores simples
                record_id = record.find('.//oai:identifier', ns)
                record_datestamp = record.find('.//oai:datestamp', ns)
                
                # Multivaluados
                setspec = [e.text for e in record.findall('.//oai:setSpec', ns)]

                records.append({
                    'record_id': record_id.text if record_id is not None else None,
                    'datestamp': record_datestamp.text if record_datestamp is not None else None,
                    'set_id': setspec,
                })

            token_elem = root.find('.//oai:resumptionToken', ns)
            if token_elem is not None:
                complete_list_size = int(token_elem.get('completeListSize'))
                resumption_token = token_elem.text

            # guarda el tamaño en el df de sets
            df_set.loc[df_set["setSpec"] == set_id, "completeListSize"] = (
                int(complete_list_size) if complete_list_size is not None else None
            )
          
    df = pd.DataFrame(records)

    timestamp = pd.Timestamp.now(tz="UTC").normalize()
    df['extract_datetime'] = timestamp

    return df, df_set, df.head(100)

In [ ]:
df_identifiers, df_col_dev, df_dev = oai_extract_identifiers_by_sets(base_url, context, env, df_cols)

Consultando: https://ri.conicet.gov.ar/oai//request?verb=ListIdentifiers&resumptionToken=oai_dc///col_11336_373/0


                    WARNING  /home/pablo/dev/scholar/kedro-scholar/.venv/lib/python3.10/site-packag ]8;id=751767;file:///usr/lib/python3.10/warnings.py\warnings.py]8;;\:]8;id=970702;file:///usr/lib/python3.10/warnings.py#109\109]8;;\
                             es/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified                 
                             HTTPS request is being made to host 'ri.conicet.gov.ar'. Adding                       
                             certificate verification is strongly advised. See:                                    
                             https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warni                
                             ngs                                                                                   
                               warnings.warn(                                                                      
                                                                                                                   

Sleeping for 0.18 seconds
Consultando: https://ri.conicet.gov.ar/oai//request?verb=ListIdentifiers&resumptionToken=oai_dc///col_11336_373/100


                    WARNING  /home/pablo/dev/scholar/kedro-scholar/.venv/lib/python3.10/site-packag ]8;id=637519;file:///usr/lib/python3.10/warnings.py\warnings.py]8;;\:]8;id=740595;file:///usr/lib/python3.10/warnings.py#109\109]8;;\
                             es/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified                 
                             HTTPS request is being made to host 'ri.conicet.gov.ar'. Adding                       
                             certificate verification is strongly advised. See:                                    
                             https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warni                
                             ngs                                                                                   
                               warnings.warn(                                                                      
                                                                                                                   

Sleeping for 0.19 seconds
Consultando: https://ri.conicet.gov.ar/oai//request?verb=ListIdentifiers&resumptionToken=oai_dc///col_11336_466/0


...

Sleeping for 10.19 seconds
Error: sin respuesta (intento 2/3)
Reintentando en 2.00 segundos...


[12/01/25 22:13:40] WARNING  /home/pablo/dev/scholar/kedro-scholar/.venv/lib/python3.10/site-packag ]8;id=253491;file:///usr/lib/python3.10/warnings.py\warnings.py]8;;\:]8;id=543315;file:///usr/lib/python3.10/warnings.py#109\109]8;;\
                             es/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified                 
                             HTTPS request is being made to host 'ri.conicet.gov.ar'. Adding                       
                             certificate verification is strongly advised. See:                                    
                             https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warni                
                             ngs                                                                                   
                               warnings.warn(                                                                      
                                                                                                                   

Sleeping for 10.22 seconds
Error: sin respuesta (intento 3/3)
Error al consultar: https://ri.conicet.gov.ar/oai//request?verb=ListIdentifiers&resumptionToken=oai_dc///col_11336_90324/0
Consultando: https://ri.conicet.gov.ar/oai//request?verb=ListIdentifiers&resumptionToken=oai_dc///col_11336_90325/0


[12/01/25 22:14:01] WARNING  /home/pablo/dev/scholar/kedro-scholar/.venv/lib/python3.10/site-packag ]8;id=877335;file:///usr/lib/python3.10/warnings.py\warnings.py]8;;\:]8;id=972677;file:///usr/lib/python3.10/warnings.py#109\109]8;;\
                             es/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified                 
                             HTTPS request is being made to host 'ri.conicet.gov.ar'. Adding                       
                             certificate verification is strongly advised. See:                                    
                             https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warni                
                             ngs                                                                                   
                               warnings.warn(                                                                      
                                                                                                                   

Sleeping for 10.34 seconds


In [ ]:
df_col_dev

setSpec            setName  col_set  com_set  completeListSize
0  col_11336_373  Articulos(BIOMED)     True    False             377.0
1  col_11336_466   Articulos(CADIC)     True    False            1615.0

In [ ]:
df_identifiers

record_id             datestamp  \
0     oai:ri.conicet.gov.ar:11336/15260  2023-03-09T02:44:18Z   
1    oai:ri.conicet.gov.ar:11336/266352  2025-07-17T11:08:26Z   
2     oai:ri.conicet.gov.ar:11336/15225  2024-09-20T17:52:07Z   
3    oai:ri.conicet.gov.ar:11336/133626  2021-12-17T12:37:25Z   
4     oai:ri.conicet.gov.ar:11336/15215  2023-03-09T02:44:18Z   
..                                  ...                   ...   
395  oai:ri.conicet.gov.ar:11336/231502  2024-03-25T15:48:37Z   
396   oai:ri.conicet.gov.ar:11336/63660  2020-12-09T16:51:03Z   
397  oai:ri.conicet.gov.ar:11336/247075  2024-11-01T13:17:20Z   
398  oai:ri.conicet.gov.ar:11336/241723  2024-10-08T15:31:13Z   
399   oai:ri.conicet.gov.ar:11336/12798  2017-02-09T18:15:43Z   

                                                set_id  \
0    [com_11336_390, com_11336_371, com_11336_372, ...   
1    [com_11336_372, com_11336_371, com_11336_394, ...   
2    [com_11336_372, com_11336_371, com_11336_390, ...   
3    [com_11336_372, com_11336_371, col_11336_373, ...   
4    [com_11336_390, com_11336_371, com_11336_100, ...   
..                                                 ...   
395  [com_11336_465, com_11336_464, com_11336_14309...   
396  [com_11336_465, com_11336_464, col_11336_466, ...   
397  [com_11336_465, com_11336_464, col_11336_466, ...   
398  [com_11336_465, com_11336_464, com_11336_169, ...   
399  [com_11336_35, com_11336_14, com_11336_465, co...   

             extract_datetime  
0   2025-11-28 00:00:00+00:00  
1   2025-11-28 00:00:00+00:00  
2   2025-11-28 00:00:00+00:00  
3   2025-11-28 00:00:00+00:00  
4   2025-11-28 00:00:00+00:00  
..                        ...  
395 2025-11-28 00:00:00+00:00  
396 2025-11-28 00:00:00+00:00  
397 2025-11-28 00:00:00+00:00  
398 2025-11-28 00:00:00+00:00  
399 2025-11-28 00:00:00+00:00  

[400 rows x 4 columns]